In [1]:
import numpy as np
import pandas as pd
from scipy.io import loadmat
import networkx as nx
import matplotlib.pyplot as plt
%matplotlib inline

import seaborn as sns
from collections import Counter
import json
import warnings
import re
warnings.filterwarnings('ignore')
import random
import statistics

from scipy.linalg import solve
import scipy
# import igraph as ig
from scipy.sparse import linalg as sla

In [2]:
def get_mat_file_info(filename):
    mat_file=loadmat(filename)
    # Get the number of files
    files=mat_file['dbs']['filename'].shape[1]
    file_names=[]
    for fi in range(files):
        file_names.append(mat_file['dbs']['filename'][0][fi][0])
    return file_names


# Choose file
## focusing on Head-tail for now 
filename='../data/mat_files/dbs_Head-Tail_20191013.mat'


# # Get filenames
files=get_mat_file_info(filename)

#dividing up the groups into 4
CCvsCC_female = []
FCvsCC_female = [] 
CCvsCC_male = [] 
FCvsCC_male = []
NacvsCC_male = []

for file in files:
#     print(file)
    if 'Female-CCvsCC' in file:
        CCvsCC_female.append(file)
    elif 'Female-FCvsCC' in file:
        FCvsCC_female.append(file)
    elif 'Male-CCvsCC' in file:
        CCvsCC_male.append(file) 
    elif 'Male-FCvsCC' in file:
        FCvsCC_male.append(file)  
    else:
        NacvsCC_male.append(file)
all_treatments = [CCvsCC_female, FCvsCC_female, CCvsCC_male, FCvsCC_male, NacvsCC_male]
print("Number of files for female-CCvsCC: " + str(len(CCvsCC_female)))
print("Number of files for female-FCvsCC: " + str(len(FCvsCC_female)))
print("Number of files for male-CCvsCC: " + str(len(CCvsCC_male)))
print("Number of files for male-FCvsCC: " + str(len(FCvsCC_male)))
print("Number of files for male-NACvsCC: " + str(len(NacvsCC_male)))


Number of files for female-CCvsCC: 10
Number of files for female-FCvsCC: 12
Number of files for male-CCvsCC: 12
Number of files for male-FCvsCC: 8
Number of files for male-NACvsCC: 8


In [3]:
#from https://rdrr.io/cran/igraph/src/R/structural.properties.R#sym-bonpow.dense
def bonacich_power_centrality(graph,exponent,tol,rescale):

    vg = 6 #number of mice

    #convert to matrix
    d = nx.to_scipy_sparse_matrix(graph)

    #adjacency matrix of size 6 (number of mice)
    id =np.identity(vg)
    
    degree_out = graph.out_degree()
    xarr = np.array(degree_out)
    degree_out_array = np.array([xarr[0][1],xarr[1][1],xarr[2][1],xarr[3][1],xarr[4][1],xarr[5][1]])
    degree_out_array = degree_out_array.astype(np.float)
    

    if round(np.linalg.det(id-(exponent*d))) == 0:
        return {}
    
    lu = sla.splu(id-(exponent*d))
    x = lu.solve(degree_out_array)
    
    if rescale:
        x = x/sum(x)
    else:
        x = x * (np.sqrt(vg/sum(x**2)))
        
    d =  {}
    for i in range(6):
        d[xarr[i][0]] = x[i]
    return d

In [4]:
def matlab_rand_net(in_deg,out_deg):

    n = len(in_deg)
    k = np.sum(in_deg).astype(np.int64)
    inInv = np.zeros((k,))
    outInv = np.zeros((k,))
    iIn = 0
    iOut = 0;

    for i in range(n):
        inInv[iIn:iIn+in_deg[i] ] = i+1
        outInv[iOut:iOut+out_deg[i] ] = i+1
        iIn = iIn+in_deg[i]
        iOut = iOut+out_deg[i]
    cij = np.eye(n).astype(np.int64)
    flag=-5
    edges = np.vstack([np.transpose(outInv[:k]), np.transpose(inInv[np.arange(k)])]).astype(np.int64)
    edges=edges-1
    for i in range(k):
        if cij[edges[0,i],edges[1,i]]==1:
            warningCounter = 1
            while 1:
                switchTo = np.random.randint(k)
                s=0
                if cij[edges[0,i],edges[1,switchTo]] ==0 and cij[edges[0,switchTo],edges[1,i]] ==0:
                    cij[edges[0,i],edges[1,switchTo]] = 1
                    if switchTo <= i:
                        cij[edges[0,switchTo],edges[1,switchTo]] = 0
                        cij[edges[0,switchTo],edges[1,i]] = 1
                    temp = edges[1,i]
                    edges[1,i] = edges[1,switchTo]
                    edges[1,switchTo] = temp;
                    break
                
                warningCounter = warningCounter+1;
                if warningCounter == 2*k^2:
                    flag = False
                    return cij,flag
        else:
            cij[edges[0,i],edges[1,i]] = 1
    cij = cij - np.eye(n)
    if flag==-5:
        flag=True
    return cij,flag

def nx_from_connectivity(A):
    G=nx.DiGraph()
    for i in range(np.shape(A)[0]):
        G.add_node(i)
    edges=np.where(A)
    for i in range(len(edges[0])):
        G.add_edge(edges[0][i],edges[1][i])
    return G

## Functions that calculate Z-Scores (Total or Divided in 2 groups)

In [5]:
def calculate_score(raw, network_measure_func, H,nrand, exponent, tol,rescale):
    din=list(d for n, d in H.in_degree())
    dout = list(d for n, d in H.out_degree())
    
    #calculate network measure of 10000 random networks
    
    rand_values=np.zeros((nrand,))
    if network_measure_func == "NA":
        b = (bonacich_power_centrality(H,exponent,tol,rescale)).values()
    else:
        b = (network_measure_func(H)).values()
    
    raw_value=np.nanmean(list(b))
    
    if raw:
        return raw_value
    
    if network_measure_func == "NA" and not raw:
#         print("z-score all bonacich")
        results=np.zeros((6,1000))
        for i in range(nrand):
            done=False
            while not done:
                try:
                    #results[:,i] gets column i
                    results[:,i]=np.array(list(bonacich_power_centrality(nx.directed_configuration_model(din, dout, create_using=nx.DiGraph()), exponent, tol, rescale).values()))
                    done=True
                except:
                    False

        z_score = (np.mean((results[:,1]-np.mean(results[:,1:],1))/np.std(results[:,1:])))
        return z_score
    
    
    for i in range(nrand):
        flag=False
        while flag==False:
            rnet,flag=matlab_rand_net(din,dout)
        D = nx_from_connectivity(rnet)
        if network_measure_func == "NA":
            b = (bonacich_power_centrality(D,exponent,tol,rescale)).values()
        else:
            b = (network_measure_func(D)).items()
                
        rand_values[i] = np.nanmean(list(b))
    
    if np.round(statistics.stdev(rand_values)*1000) != 0:
        z_score = (raw_value- np.nanmean(rand_values)) / (np.std(rand_values)) 
    else:
        z_score = np.nan
    return z_score

def measures_individual(raw, network_measure_func, H, nrand, exponent, tol, rescale):
    if network_measure_func == "NA":
        H_items = (bonacich_power_centrality(H,exponent,tol,rescale)).items()
    else:
        H_items = (network_measure_func(H)).items()
    if raw:
        return H_items

def measures_CCvsCC(raw, network_measure_func, H, nrand, exponent, tol,rescale):

    #calculate actual network measures
    d_network = {'CC-1': [], 'CC-2': []}
    if network_measure_func == "NA":
        H_items = (bonacich_power_centrality(H,exponent,tol,rescale)).items()
    else:
        H_items = (network_measure_func(H)).items()
    
    print(H_items)
    for key, value in H_items:   
        if key in ['CC1_1', 'CC1_2', 'CC1_3']:
            d_network['CC-1'].append(value)
        else:
            d_network['CC-2'].append(value)
    
    raw_value_CC1=np.nanmean(list(d_network['CC-1']))
    raw_value_CC2=np.nanmean(list(d_network['CC-2'])) 
  
    if raw:
        return [raw_value_CC1, raw_value_CC2]
    
    #calculate random network measures 
    rand_values_CC1=np.zeros((nrand,))
    rand_values_CC2=np.zeros((nrand,))

    
    din=list(d for n, d in H.in_degree())
    dout = list(d for n, d in H.out_degree())
  
    for i in range(nrand):
        #reset random dicts every iteration 
        d_random = {'CC-1': [], 'CC-2': []}
    
        
        flag=False
        while flag==False:
            rnet,flag=matlab_rand_net(din,dout)
        
        random_nodes = list(random.sample(H.nodes,len(H.nodes)))
        map_nodes = {} 
        for count, node in enumerate(random_nodes):
            map_nodes[count] = node
        
        D = nx_from_connectivity(rnet)
        D =nx.relabel_nodes(D,map_nodes)
        
        if network_measure_func == "NA":
            d_items = (bonacich_power_centrality(D,exponent,tol,rescale)).items()
        else:
            d_items = (network_measure_func(D)).items()
        
        #calculate network measure
        for key, value in d_items:
            if key in ['CC1_1', 'CC1_2', 'CC1_3']:
                d_random['CC-1'].append(value)
            else:
                d_random['CC-2'].append(value)
            
        rand_values_CC1[i] = np.nanmean(list(d_random['CC-1']))
        rand_values_CC2[i] = np.nanmean(list(d_random['CC-1']))
        
    
    if np.round(statistics.stdev(rand_values_CC1)*1000) != 0:
        z_score_CC1 = (raw_value_CC1 -np.nanmean(rand_values_CC1)) / (np.std(rand_values_CC1)) 
    else:
        z_score_CC1 = np.nan

    
    if np.round(statistics.stdev(rand_values_CC2)*1000) != 0:
        z_score_CC2 = (raw_value_CC2- np.nanmean(rand_values_CC2)) / (np.std(rand_values_CC2)) 
    else:
        z_score_CC2 = np.nan
        
    return [z_score_CC1, z_score_CC2]
        
        
def measures_NACvsCC(raw, network_measure_func, H, nrand, exponent, tol,rescale):
    
    #calculate actual network measures
    d_network = {'CC': [], 'NAC': []}
    
    if network_measure_func == "NA":
        H_items = (bonacich_power_centrality(H,exponent,tol,rescale)).items()
    else:
        H_items = (network_measure_func(H)).items()
#     print(H_items)
    for key, value in H_items:   
#         print(key)
        if "CC" in str(key):
            d_network['CC'].append(value)
        elif "Nac" in str(key):
            d_network['NAC'].append(value)
    
    raw_value_NAC=np.nanmean(list(d_network['NAC']))
    raw_value_CC=np.nanmean(list(d_network['CC'])) 

    if raw:
        return [raw_value_CC, raw_value_NAC]
    
    #calculate random network measures 
    rand_values_CC=np.zeros((nrand,))
    rand_values_NAC=np.zeros((nrand,))
    
    din=list(d for n, d in H.in_degree())
    dout = list(d for n, d in H.out_degree())
  
    for i in range(nrand):
        #reset random dicts every iteration 
        d_random = {'CC': [], 'NAC': []}
        

        flag=False
        while flag==False:
            rnet,flag=matlab_rand_net(din,dout)
        
        random_nodes = list(random.sample(H.nodes,len(H.nodes)))
        map_nodes = {} 
        for count, node in enumerate(random_nodes):
            map_nodes[count] = node
        
        D = nx_from_connectivity(rnet)
        D =nx.relabel_nodes(D,map_nodes)
        
        
        
        if network_measure_func == "NA":
            d_items = (bonacich_power_centrality(D,exponent,tol,rescale)).items()
        else:
            d_items = (network_measure_func(D)).items()  
       
        #calculate network measure
        for key, value in d_items:
            if "CC" in key:
                d_random['CC'].append(value)
            elif "Nac" in key:
                d_random['NAC'].append(value)
            
        rand_values_CC[i] = np.nanmean(list(d_random['CC']))
        rand_values_NAC[i] = np.nanmean(list(d_random['NAC']))

    if np.round(statistics.stdev(rand_values_CC)*1000) != 0:
        z_score_CC = (raw_value_CC -np.nanmean(rand_values_CC)) / (np.std(rand_values_CC)) 
    else:
        z_score_CC = np.nan

    if np.round(statistics.stdev(rand_values_NAC)*1000) != 0:
        z_score_NAC = (raw_value_NAC- np.nanmean(rand_values_NAC)) / (np.std(rand_values_NAC)) 
    else:
        z_score_NAC = np.nan
        
    return [z_score_CC, z_score_NAC]


def measures_FCvsCC(raw, network_measure_func, H, nrand, exponent, tol,rescale):
    
    #calculate actual network measures
    d_network = {'CC': [], 'FC': []}
    if network_measure_func == "NA":
        H_items = (bonacich_power_centrality(H,exponent,tol,rescale)).items()
    else:
        H_items = (network_measure_func(H)).items()
    
    for key, value in H_items:   
        if "FC" in key:
            d_network['FC'].append(value)
        elif "CC" in key:
            d_network['CC'].append(value)
    
    raw_value_FC=np.nanmean(list(d_network['FC']))
    raw_value_CC=np.nanmean(list(d_network['CC'])) 

    if raw: 
        return [raw_value_CC, raw_value_FC]
    #calculate random network measures 
    rand_values_CC=np.zeros((nrand,))
    rand_values_FC=np.zeros((nrand,))
    
    din=list(d for n, d in H.in_degree())
    dout = list(d for n, d in H.out_degree())
  
    for i in range(nrand):
        #reset random dicts every iteration 
        d_random = {'CC': [], 'FC': []}
        
        flag=False
        while flag==False:
            rnet,flag=matlab_rand_net(din,dout)
        
        random_nodes = list(random.sample(H.nodes,len(H.nodes)))
        map_nodes = {} 
        for count, node in enumerate(random_nodes):
            map_nodes[count] = node
        
        D = nx_from_connectivity(rnet)
        D =nx.relabel_nodes(D,map_nodes)
        
        if network_measure_func == "NA":
            d_items = (bonacich_power_centrality(D,exponent,tol,rescale)).items()
        else:
            d_items = (network_measure_func(D)).items()
        
        #calculate network measure
        for key, value in d_items:
            if "CC" in key:
                d_random['CC'].append(value)
            elif "FC" in key:
                d_random['FC'].append(value)
            
        rand_values_CC[i] = np.nanmean(list(d_random['CC']))
        rand_values_FC[i] = np.nanmean(list(d_random['FC']))
        
    
    if np.round(statistics.stdev(rand_values_CC)*1000) != 0:
        z_score_CC = (raw_value_CC -np.nanmean(rand_values_CC)) / (np.std(rand_values_CC)) 
    else:
        z_score_CC = np.nan

    
    if np.round(statistics.stdev(rand_values_FC)*1000) != 0:
        z_score_FC = (raw_value_FC- np.nanmean(rand_values_FC)) / (np.std(rand_values_FC)) 
    else:
        z_score_FC = np.nan
        
    return [z_score_CC, z_score_FC]



In [6]:
def load_iterations_from_mat_file(filename,file):
    mat_file=loadmat(filename)
    # Get the number of files
    files=mat_file['dbs']['filename'].shape[1]
    file_names=[]
    for fi in range(files):
        file_names.append(mat_file['dbs']['filename'][0][fi][0])
    file_num=np.where(np.array(file_names)==file)[0][0]
        
    if len(mat_file['dbs']['networks'][0][file_num].shape)<3:
        mat_file['dbs']['networks'][0][file_num]=mat_file['dbs']['networks'][0][file_num][:,:,np.newaxis]
        
    G_list=[]
    # Get the number of mice
    nmice=mat_file['dbs']['networks'][0][file_num][:,:,0].shape[0]
    # Get the ids
    ids_t=mat_file['dbs']['ids'][0][file_num][0]
    ids=[]
    for id in range(nmice):
        ids.append(ids_t[id][0])
    types=np.unique(ids)
    type_count=np.ones((len(types),),np.int64)
    mapping = {}
    for i in range(nmice):
        mapping[i]=ids[i]+'_'+str(type_count[np.where(types==ids[i])[0]][0])
        type_count[np.where(types==ids[i])[0]]+=1
    # Get the number of iterations
    iters=mat_file['dbs']['networks'][0][file_num].shape[2]
    
    
    # Make the graph
    for iter in range(iters):
        mat_net=mat_file['dbs']['networks'][0][file_num][:,:,iter]
        mat_net[mat_net>0]=1
        G=nx.from_numpy_matrix(mat_net,create_using=nx.DiGraph())
        G=nx.relabel_nodes(G,mapping)
        G_list.append(G)
    return G_list



def get_values(treatment_file, interaction_file):
    lst = [] 
    if 'Female-CCvsCC' in treatment_file:
        lst = ['Female', 'CCvsCC']
    elif 'Female-FCvsCC' in treatment_file:
        lst = ['Female', 'FCvsCC']
    elif 'Male-CCvsCC' in treatment_file:
        lst = ['Male', 'CCvsCC']
    elif 'Male-FCvsCC' in treatment_file:
        lst = ['Male', 'FCvsCC']
    elif 'NacvsCC' in treatment_file:
        lst = ['Male', 'NACvsCC']
    if 'Head-Tail' in interaction_file:
        return lst + ['Head-Tail']
    if 'Head-Head' in interaction_file:
        return lst + ['Head-Head']
    if 'Centers-Close' in interaction_file:
        return lst + ['Centers-Close']
    if 'Oriented-Towards' in interaction_file:
        return lst + ['Oriented-Towards']

def all_treatment_analysis(treatments, All, network_measures, reverse, exponent, tol, rescale, raw, random_iterations):
    date = "20191310"
    print("Properties of current analysis:")
    print("Raw: ", str(raw))
    print("Split groups calculation: ", str(not All))
    print("Network Measure: ", str(network_measures[0][0]))
    print("----------------------")
    df_all = pd.DataFrame([], columns = ['Network Measure', 'Score', 'Interaction', 'Gender', 'Strain', 'Group', 'File', 'Iteration', 'Total_Iterations'])
    df_split = pd.DataFrame([], columns = ['Network Measure', 'Score', 'Interaction', 'Gender', 'Strain', 'Care', 'Group', 'File', 'Iteration', 'Total_Iterations'])
    if raw:
        type = "raw_"
    else:
        type = "_z-score_" + str(random_iterations) + "_"
    if network_measures[0][1] == "NA":
        type += "exponent_" + str(exponent)
        
    for treatment in treatments: 
    
        # Get filenames
        files=get_mat_file_info(treatment)
    
        #dividing up the groups into 4
        CCvsCC_female, FCvsCC_female, CCvsCC_male, FCvsCC_male, NACvsCC_male  = ([] for i in range(5))
        for file in files:
            if 'Female-CCvsCC' in file:
                CCvsCC_female.append(file)
            elif 'Female-FCvsCC' in file:
                FCvsCC_female.append(file)
            elif 'Male-CCvsCC' in file:
                CCvsCC_male.append(file) 
            elif 'Male-FCvsCC' in file:
                FCvsCC_male.append(file)
            elif 'Male-NacvsCC' in file:
                NACvsCC_male.append(file)
        all_treatments = [NACvsCC_male, CCvsCC_female, FCvsCC_female, CCvsCC_male, FCvsCC_male]
        total_iterations = 0
        t = 1
        for x in range(len(all_treatments)):
            mean_trial_raw = {}
            mean_trial_zscore = {} 
            for i in range(len(all_treatments[x])):
                file=all_treatments[x][i]
                print(file)
                print(treatment)
                
                stability_all = pd.DataFrame([], columns = ['Network Measure', 'Score', 'Interaction', 'Gender', 'Strain', 'Group', 'File', 'Iteration', 'Total_Iterations'])
                stability_split = pd.DataFrame([], columns = ['Network Measure', 'Score', 'Interaction', 'Gender', 'Strain', 'Care', 'Group', 'File', 'Iteration', 'Total_Iterations'])
                
                # Get the network measures
                G_list=load_iterations_from_mat_file(treatment,file)
                
                
                df_all_temp = pd.DataFrame([], columns = ['Network Measure', 'Score', 'Interaction', 'Gender', 'Strain', 'Group', 'File', 'Iteration', 'Total_Iterations'])
                df_split_temp_1 = pd.DataFrame([], columns = ['Network Measure', 'Score', 'Interaction', 'Gender', 'Strain', 'Care', 'Group', 'File', 'Iteration', 'Total_Iterations'])
                df_split_temp_2 = pd.DataFrame([], columns = ['Network Measure', 'Score', 'Interaction', 'Gender', 'Strain', 'Care', 'Group', 'File', 'Iteration', 'Total_Iterations'])

                
                for ii in range(len(G_list)):
                    
                    #G_list is total number of iterations
                    
                    
                    gender, strain, interaction = get_values(all_treatments[x][i], treatment)

                    total_iterations += 1

                    G=G_list[ii]
                    if len(G_list) == 26 and ii == 7:
                        continue
                     
                    
                    if All:
                        #calculate z-score for all network, and add to df_zscore
                        for i in range(len(network_measures)):
                            z_score = calculate_score(raw, network_measures[i][1],G,random_iterations,exponent,tol,rescale) 
                            df_all_temp.loc[len(df_all_temp)]=[network_measures[i][0], z_score, interaction, gender, strain, t, file, ii+1, len(G_list)]
                            stability_all.loc[len(stability_all)] = [network_measures[i][0], z_score, interaction, gender, strain, t, file, ii+1, len(G_list)]
                    else:                         
                            
                        #split z-score into FC and CC or CC1 and CC2, add to df_zscore  
                        individual = measures_individual(raw, network_measures[0][1], G, random_iterations, exponent,tol,rescale)
                        for name, score in individual:
                            df_split_temp_1.loc[len(df_split_temp_1)]=[network_measures[0][0], score, interaction, gender, strain, name, t, file, ii+1, len(G_list)]
#                             df_split_temp_1.loc[len(df_split_temp_1)]=[network_measures[0][0], score_CC, interaction, gender, strain, "CC", t, file, ii+1, len(G_list)]
#                             df_split_temp_2.loc[len(df_split_temp_2)]=[network_measures[0][0], score_NAC, interaction, gender, strain, "NAC", t, file, ii+1, len(G_list)]
                        
#                         elif strain == "CCvsCC":
#                             score_CC1, score_CC2 = measures_CCvsCC(raw, network_measures[0][1], G, random_iterations, exponent,tol,rescale)
#                             df_split_temp_1.loc[len(df_split_temp_1)]=[network_measures[0][0], score_CC1, interaction, gender, strain, "CC1", t, file, ii+1, len(G_list)]
#                             df_split_temp_2.loc[len(df_split_temp_2)]=[network_measures[0][0], score_CC2, interaction, gender, strain, "CC2", t, file, ii+1, len(G_list)]
                        
#                         elif strain == "FCvsCC":
#                             score_CC, score_FC = measures_FCvsCC(raw, network_measures[0][1], G, random_iterations ,exponent,tol,rescale)
#                             df_split_temp_1.loc[len(df_split_temp_1)]=[network_measures[0][0], score_CC, interaction, gender, strain, "CC", t, file, ii+1, len(G_list)]
#                             df_split_temp_2.loc[len(df_split_temp_2)]=[network_measures[0][0], score_FC, interaction, gender, strain, "FC", t, file, ii+1, len(G_list)]
                t+= 1
                print(df_split_temp_1)
                if All:
                    name = "_" + str(type) + str(interaction) + "_" + str(gender) + "_" + str(strain) + "_" + str(str(network_measures[0][0]).replace(" ", "")) + ".csv"
                    print("------------------------------- name " + str(name))
                    df_all_temp.to_csv("../data/consistency/" + str(str(network_measures[0][0]).replace(" ", "_")) + "/consistency_ALL" + str(name))

#                     new_list = (df_all_temp.iloc[0]).tolist()
#                     if df_all_temp['Score'].mean() == 0:
#                         print(df_all_temp['Score'])
#                     new_list[1] = df_all_temp["Score"].mean()
#                     print(new_list)

#                     df_all_zscore.loc[len(df_all_zscore)]=new_list
                    df_all_temp = pd.DataFrame([], columns = ['Network Measure', 'Score', 'Interaction', 'Gender', 'Strain', 'Group', 'File', 'Iteration', 'Total_Iterations'])
#                     df_all_zscore.to_csv("../data/temp_ALL_score.csv")
                    
                else: 
#                     frames = [df_split_temp_1, df_split_temp_2]
#                     result = pd.concat(frames)
                    name = "_individual_" + str(type) + str(interaction) + "_" + str(gender) + "_" + str(strain) + "_" + str(str(network_measures[0][0]).replace(" ", "_")) + ".csv"
                    print("------------------------------- name " + str(name))

                    df_split_temp_1.to_csv("../data/consistency/" + str(str(network_measures[0][0]).replace(" ", "_")) + "/consistency_SPLIT" + str(name))
                                               
                    df_split_temp_1 = pd.DataFrame([], columns = ['Network Measure', 'Score', 'Interaction', 'Gender', 'Strain', 'Group', 'File', 'Iteration', 'Total_Iterations'])
                                        
                    df_split_temp_2 = pd.DataFrame([], columns = ['Network Measure', 'Score', 'Interaction', 'Gender', 'Strain', 'Group', 'File', 'Iteration', 'Total_Iterations'])
                        


In [19]:
# %%time
# # def all_treatment_analysis(treatments, All, network_measures, reverse, exponent, tol, rescale, raw, iterations):
# # treatments = [["./data/dbs_Head-Tail_20191013.mat"], ["./data/dbs_Head-Head_20191013.mat"], ["./data/dbs_Centers-Close_20191013.mat"], ["./data/dbs_Oriented-Towards_20191013.mat"]]
# treatments = [['../data/mat_files/dbs_Head-Tail_20191013.mat']]
# for x in treatments:
#     print(x)
#     df_zscore_ev_split = all_treatment_analysis(x, False, [['eigenvector centrality', nx.eigenvector_centrality_numpy]], False, 0, 1e-07,True, True, 0)

['../data/mat_files/dbs_Head-Tail_20191013.mat']
Properties of current analysis:
Raw:  True
Split groups calculation:  True
Network Measure:  eigenvector centrality
----------------------
fixed_Male-NacvsCC_3vs3Males_P60_CCvsNAC_Group8V_Interaction_30min_cam_2_Sat_09_07_2019_mjpeg_tracks.mat
../data/mat_files/dbs_Head-Tail_20191013.mat
fixed_Male-NacvsCC_3vs3Males_P60_CCvsNAC_Group8V_Interaction_30min_cam_2_Sat_09_07_2019_mjpeg_tracks.mat
CC_1
-3.841724429933899e-17
CC_2
0.5211212421739552
CC_3
0.5211212421739552
Nac_1
0.3555755127006844
Nac_2
0.24261905867607989
Nac_3
0.5211212421739554


TypeError: list indices must be integers or slices, not str

In [8]:
%%time
# def all_treatment_analysis(treatments, All, network_measures, reverse, exponent, tol, rescale, raw, iterations):
treatments = [["../data/mat_files/dbs_Head-Tail_20191013.mat"], ["../data/mat_files/dbs_Head-Head_20191013.mat"], ["../data/mat_files/dbs_Centers-Close_20191013.mat"], ["../data/mat_files/dbs_Oriented-Towards_20191013.mat"]]
# treatments = [['../data/mat_files/dbs_Head-Tail_20191013.mat']]
for x in treatments:
    print(x)
    df_zscore_ev_split = all_treatment_analysis(x, False, [['betweenness centrality', nx.betweenness_centrality]], False, 0, 1e-07,True, True, 0)

['../data/mat_files/dbs_Head-Tail_20191013.mat']
Properties of current analysis:
Raw:  True
Split groups calculation:  True
Network Measure:  betweenness centrality
----------------------
fixed_Male-NacvsCC_3vs3Males_P60_CCvsNAC_Group8V_Interaction_30min_cam_2_Sat_09_07_2019_mjpeg_tracks.mat
../data/mat_files/dbs_Head-Tail_20191013.mat
            Network Measure  Score Interaction Gender   Strain   Care Group  \
0    betweenness centrality  0.000   Head-Tail   Male  NACvsCC   CC_1     1   
1    betweenness centrality  0.150   Head-Tail   Male  NACvsCC   CC_2     1   
2    betweenness centrality  0.000   Head-Tail   Male  NACvsCC   CC_3     1   
3    betweenness centrality  0.100   Head-Tail   Male  NACvsCC  Nac_1     1   
4    betweenness centrality  0.150   Head-Tail   Male  NACvsCC  Nac_2     1   
..                      ...    ...         ...    ...      ...    ...   ...   
103  betweenness centrality  0.000   Head-Tail   Male  NACvsCC   CC_2     1   
104  betweenness centrality  0

            Network Measure  Score Interaction Gender   Strain   Care Group  \
0    betweenness centrality   0.00   Head-Tail   Male  NACvsCC   CC_1     6   
1    betweenness centrality   0.00   Head-Tail   Male  NACvsCC   CC_2     6   
2    betweenness centrality   0.00   Head-Tail   Male  NACvsCC   CC_3     6   
3    betweenness centrality   0.15   Head-Tail   Male  NACvsCC  Nac_1     6   
4    betweenness centrality   0.30   Head-Tail   Male  NACvsCC  Nac_2     6   
..                      ...    ...         ...    ...      ...    ...   ...   
139  betweenness centrality   0.00   Head-Tail   Male  NACvsCC   CC_2     6   
140  betweenness centrality   0.30   Head-Tail   Male  NACvsCC   CC_3     6   
141  betweenness centrality   0.00   Head-Tail   Male  NACvsCC  Nac_1     6   
142  betweenness centrality   0.45   Head-Tail   Male  NACvsCC  Nac_2     6   
143  betweenness centrality   0.35   Head-Tail   Male  NACvsCC  Nac_3     6   

                                                  F

           Network Measure  Score Interaction  Gender  Strain   Care Group  \
0   betweenness centrality   0.05   Head-Tail  Female  CCvsCC  CC1_1    10   
1   betweenness centrality   0.00   Head-Tail  Female  CCvsCC  CC1_2    10   
2   betweenness centrality   0.00   Head-Tail  Female  CCvsCC  CC1_3    10   
3   betweenness centrality   0.00   Head-Tail  Female  CCvsCC  CC2_1    10   
4   betweenness centrality   0.00   Head-Tail  Female  CCvsCC  CC2_2    10   
5   betweenness centrality   0.00   Head-Tail  Female  CCvsCC  CC2_3    10   
6   betweenness centrality   0.00   Head-Tail  Female  CCvsCC  CC1_1    10   
7   betweenness centrality   0.00   Head-Tail  Female  CCvsCC  CC1_2    10   
8   betweenness centrality   0.00   Head-Tail  Female  CCvsCC  CC1_3    10   
9   betweenness centrality   0.00   Head-Tail  Female  CCvsCC  CC2_1    10   
10  betweenness centrality   0.00   Head-Tail  Female  CCvsCC  CC2_2    10   
11  betweenness centrality   0.00   Head-Tail  Female  CCvsCC  C

           Network Measure  Score Interaction  Gender  Strain   Care Group  \
0   betweenness centrality  0.000   Head-Tail  Female  CCvsCC  CC1_1    11   
1   betweenness centrality  0.000   Head-Tail  Female  CCvsCC  CC1_2    11   
2   betweenness centrality  0.150   Head-Tail  Female  CCvsCC  CC1_3    11   
3   betweenness centrality  0.000   Head-Tail  Female  CCvsCC  CC2_1    11   
4   betweenness centrality  0.100   Head-Tail  Female  CCvsCC  CC2_2    11   
5   betweenness centrality  0.100   Head-Tail  Female  CCvsCC  CC2_3    11   
6   betweenness centrality  0.050   Head-Tail  Female  CCvsCC  CC1_1    11   
7   betweenness centrality  0.000   Head-Tail  Female  CCvsCC  CC1_2    11   
8   betweenness centrality  0.150   Head-Tail  Female  CCvsCC  CC1_3    11   
9   betweenness centrality  0.000   Head-Tail  Female  CCvsCC  CC2_1    11   
10  betweenness centrality  0.100   Head-Tail  Female  CCvsCC  CC2_2    11   
11  betweenness centrality  0.150   Head-Tail  Female  CCvsCC  C

           Network Measure  Score Interaction  Gender  Strain   Care Group  \
0   betweenness centrality   0.00   Head-Tail  Female  CCvsCC  CC1_1    13   
1   betweenness centrality   0.00   Head-Tail  Female  CCvsCC  CC1_2    13   
2   betweenness centrality   0.10   Head-Tail  Female  CCvsCC  CC1_3    13   
3   betweenness centrality   0.15   Head-Tail  Female  CCvsCC  CC2_1    13   
4   betweenness centrality   0.00   Head-Tail  Female  CCvsCC  CC2_2    13   
5   betweenness centrality   0.00   Head-Tail  Female  CCvsCC  CC2_3    13   
6   betweenness centrality   0.00   Head-Tail  Female  CCvsCC  CC1_1    13   
7   betweenness centrality   0.00   Head-Tail  Female  CCvsCC  CC1_2    13   
8   betweenness centrality   0.05   Head-Tail  Female  CCvsCC  CC1_3    13   
9   betweenness centrality   0.15   Head-Tail  Female  CCvsCC  CC2_1    13   
10  betweenness centrality   0.00   Head-Tail  Female  CCvsCC  CC2_2    13   
11  betweenness centrality   0.05   Head-Tail  Female  CCvsCC  C

...

             Network Measure  Score       Interaction Gender  Strain   Care  \
0     betweenness centrality  0.025  Oriented-Towards   Male  CCvsCC  CC1_1   
1     betweenness centrality  0.025  Oriented-Towards   Male  CCvsCC  CC1_2   
2     betweenness centrality  0.000  Oriented-Towards   Male  CCvsCC  CC1_3   
3     betweenness centrality  0.000  Oriented-Towards   Male  CCvsCC  CC2_1   
4     betweenness centrality  0.100  Oriented-Towards   Male  CCvsCC  CC2_2   
...                      ...    ...               ...    ...     ...    ...   
2731  betweenness centrality  0.500  Oriented-Towards   Male  CCvsCC  CC1_2   
2732  betweenness centrality  0.000  Oriented-Towards   Male  CCvsCC  CC1_3   
2733  betweenness centrality  0.200  Oriented-Towards   Male  CCvsCC  CC2_1   
2734  betweenness centrality  0.200  Oriented-Towards   Male  CCvsCC  CC2_2   
2735  betweenness centrality  0.000  Oriented-Towards   Male  CCvsCC  CC2_3   

     Group                                         

             Network Measure  Score       Interaction Gender  Strain   Care  \
0     betweenness centrality  0.050  Oriented-Towards   Male  CCvsCC  CC1_1   
1     betweenness centrality  0.075  Oriented-Towards   Male  CCvsCC  CC1_2   
2     betweenness centrality  0.000  Oriented-Towards   Male  CCvsCC  CC1_3   
3     betweenness centrality  0.000  Oriented-Towards   Male  CCvsCC  CC2_1   
4     betweenness centrality  0.000  Oriented-Towards   Male  CCvsCC  CC2_2   
...                      ...    ...               ...    ...     ...    ...   
2719  betweenness centrality  0.150  Oriented-Towards   Male  CCvsCC  CC1_2   
2720  betweenness centrality  0.000  Oriented-Towards   Male  CCvsCC  CC1_3   
2721  betweenness centrality  0.000  Oriented-Towards   Male  CCvsCC  CC2_1   
2722  betweenness centrality  0.300  Oriented-Towards   Male  CCvsCC  CC2_2   
2723  betweenness centrality  0.200  Oriented-Towards   Male  CCvsCC  CC2_3   

     Group                                         

             Network Measure  Score       Interaction Gender  Strain   Care  \
0     betweenness centrality   0.05  Oriented-Towards   Male  CCvsCC  CC1_1   
1     betweenness centrality   0.00  Oriented-Towards   Male  CCvsCC  CC1_2   
2     betweenness centrality   0.00  Oriented-Towards   Male  CCvsCC  CC1_3   
3     betweenness centrality   0.00  Oriented-Towards   Male  CCvsCC  CC2_1   
4     betweenness centrality   0.00  Oriented-Towards   Male  CCvsCC  CC2_2   
...                      ...    ...               ...    ...     ...    ...   
2833  betweenness centrality   0.05  Oriented-Towards   Male  CCvsCC  CC1_2   
2834  betweenness centrality   0.30  Oriented-Towards   Male  CCvsCC  CC1_3   
2835  betweenness centrality   0.15  Oriented-Towards   Male  CCvsCC  CC2_1   
2836  betweenness centrality   0.20  Oriented-Towards   Male  CCvsCC  CC2_2   
2837  betweenness centrality   0.00  Oriented-Towards   Male  CCvsCC  CC2_3   

     Group                                         

             Network Measure  Score       Interaction Gender  Strain  Care  \
0     betweenness centrality  0.000  Oriented-Towards   Male  FCvsCC  CC_1   
1     betweenness centrality  0.000  Oriented-Towards   Male  FCvsCC  CC_2   
2     betweenness centrality  0.000  Oriented-Towards   Male  FCvsCC  CC_3   
3     betweenness centrality  0.000  Oriented-Towards   Male  FCvsCC  FC_1   
4     betweenness centrality  0.200  Oriented-Towards   Male  FCvsCC  FC_2   
...                      ...    ...               ...    ...     ...   ...   
1957  betweenness centrality  0.000  Oriented-Towards   Male  FCvsCC  CC_2   
1958  betweenness centrality  0.000  Oriented-Towards   Male  FCvsCC  CC_3   
1959  betweenness centrality  0.000  Oriented-Towards   Male  FCvsCC  FC_1   
1960  betweenness centrality  0.100  Oriented-Towards   Male  FCvsCC  FC_2   
1961  betweenness centrality  0.025  Oriented-Towards   Male  FCvsCC  FC_3   

     Group                                               File I

             Network Measure  Score       Interaction Gender  Strain  Care  \
0     betweenness centrality    0.2  Oriented-Towards   Male  FCvsCC  CC_1   
1     betweenness centrality    0.0  Oriented-Towards   Male  FCvsCC  CC_2   
2     betweenness centrality    0.2  Oriented-Towards   Male  FCvsCC  CC_3   
3     betweenness centrality    0.0  Oriented-Towards   Male  FCvsCC  FC_1   
4     betweenness centrality    0.0  Oriented-Towards   Male  FCvsCC  FC_2   
...                      ...    ...               ...    ...     ...   ...   
2725  betweenness centrality    0.0  Oriented-Towards   Male  FCvsCC  CC_2   
2726  betweenness centrality    0.0  Oriented-Towards   Male  FCvsCC  CC_3   
2727  betweenness centrality    0.1  Oriented-Towards   Male  FCvsCC  FC_1   
2728  betweenness centrality    0.0  Oriented-Towards   Male  FCvsCC  FC_2   
2729  betweenness centrality    0.0  Oriented-Towards   Male  FCvsCC  FC_3   

     Group                                               File I

In [41]:
%%time
# def all_treatment_analysis(treatments, All, network_measures, reverse, exponent, tol, rescale, raw, iterations):
# treatments = [["./data/dbs_Head-Tail_20191013.mat"], ["./data/dbs_Head-Head_20191013.mat"], ["./data/dbs_Centers-Close_20191013.mat"], ["./data/dbs_Oriented-Towards_20191013.mat"]]
treatments = [['../data/mat_files/dbs_Head-Tail_20191013.mat']]
for x in treatments:
    print(x)
    df_zscore_ev_split = all_treatment_analysis(x, False, [['clustering centrality', nx.clustering]], False, 0, 1e-07,True, True, 0)

['../data/mat_files/dbs_Head-Tail_20191013.mat']
Properties of current analysis:
Raw:  True
Split groups calculation:  True
Network Measure:  clustering centrality
----------------------
fixed_Male-NacvsCC_3vs3Males_P60_CCvsNAC_Group8V_Interaction_30min_cam_2_Sat_09_07_2019_mjpeg_tracks.mat
../data/mat_files/dbs_Head-Tail_20191013.mat


NetworkXNotImplemented: not implemented for directed type

In [9]:
%%time
# def all_treatment_analysis(treatments, All, network_measures, reverse, exponent, tol, rescale, raw, iterations):
treatments = [["../data/mat_files/dbs_Head-Tail_20191013.mat"], ["../data/mat_files/dbs_Head-Head_20191013.mat"], ["../data/mat_files/dbs_Centers-Close_20191013.mat"], ["../data/mat_files/dbs_Oriented-Towards_20191013.mat"]]
# treatments = [['../data/mat_files/dbs_Head-Tail_20191013.mat']]
for x in treatments:
    print(x)
    df_zscore_ev_split = all_treatment_analysis(x, False, [['outdegree centrality', nx.out_degree_centrality]], False, 0, 1e-07,True, True, 0)

['../data/mat_files/dbs_Head-Tail_20191013.mat']
Properties of current analysis:
Raw:  True
Split groups calculation:  True
Network Measure:  outdegree centrality
----------------------
fixed_Male-NacvsCC_3vs3Males_P60_CCvsNAC_Group8V_Interaction_30min_cam_2_Sat_09_07_2019_mjpeg_tracks.mat
../data/mat_files/dbs_Head-Tail_20191013.mat
          Network Measure  Score Interaction Gender   Strain   Care Group  \
0    outdegree centrality    0.0   Head-Tail   Male  NACvsCC   CC_1     1   
1    outdegree centrality    0.4   Head-Tail   Male  NACvsCC   CC_2     1   
2    outdegree centrality    0.0   Head-Tail   Male  NACvsCC   CC_3     1   
3    outdegree centrality    0.2   Head-Tail   Male  NACvsCC  Nac_1     1   
4    outdegree centrality    0.6   Head-Tail   Male  NACvsCC  Nac_2     1   
..                    ...    ...         ...    ...      ...    ...   ...   
103  outdegree centrality    0.2   Head-Tail   Male  NACvsCC   CC_2     1   
104  outdegree centrality    0.4   Head-Tail   M

          Network Measure  Score Interaction Gender   Strain   Care Group  \
0    outdegree centrality    0.2   Head-Tail   Male  NACvsCC   CC_1     6   
1    outdegree centrality    0.4   Head-Tail   Male  NACvsCC   CC_2     6   
2    outdegree centrality    0.2   Head-Tail   Male  NACvsCC   CC_3     6   
3    outdegree centrality    0.4   Head-Tail   Male  NACvsCC  Nac_1     6   
4    outdegree centrality    0.4   Head-Tail   Male  NACvsCC  Nac_2     6   
..                    ...    ...         ...    ...      ...    ...   ...   
139  outdegree centrality    0.2   Head-Tail   Male  NACvsCC   CC_2     6   
140  outdegree centrality    0.2   Head-Tail   Male  NACvsCC   CC_3     6   
141  outdegree centrality    0.2   Head-Tail   Male  NACvsCC  Nac_1     6   
142  outdegree centrality    0.6   Head-Tail   Male  NACvsCC  Nac_2     6   
143  outdegree centrality    0.2   Head-Tail   Male  NACvsCC  Nac_3     6   

                                                  File Iteration  \
0    fi

         Network Measure  Score Interaction  Gender  Strain   Care Group  \
0   outdegree centrality    0.4   Head-Tail  Female  CCvsCC  CC1_1    10   
1   outdegree centrality    0.2   Head-Tail  Female  CCvsCC  CC1_2    10   
2   outdegree centrality    0.0   Head-Tail  Female  CCvsCC  CC1_3    10   
3   outdegree centrality    0.4   Head-Tail  Female  CCvsCC  CC2_1    10   
4   outdegree centrality    0.0   Head-Tail  Female  CCvsCC  CC2_2    10   
5   outdegree centrality    0.6   Head-Tail  Female  CCvsCC  CC2_3    10   
6   outdegree centrality    0.4   Head-Tail  Female  CCvsCC  CC1_1    10   
7   outdegree centrality    0.0   Head-Tail  Female  CCvsCC  CC1_2    10   
8   outdegree centrality    0.0   Head-Tail  Female  CCvsCC  CC1_3    10   
9   outdegree centrality    0.4   Head-Tail  Female  CCvsCC  CC2_1    10   
10  outdegree centrality    0.0   Head-Tail  Female  CCvsCC  CC2_2    10   
11  outdegree centrality    0.8   Head-Tail  Female  CCvsCC  CC2_3    10   
12  outdegre

fixed_Female-CCvsCC_3vs3Females_P60_CCvsCC_Group4L_interaction_30min_cam_2_Thu_03_28_2019_mjpeg_tracks.mat
../data/mat_files/dbs_Head-Tail_20191013.mat
          Network Measure  Score Interaction  Gender  Strain   Care Group  \
0    outdegree centrality    0.0   Head-Tail  Female  CCvsCC  CC1_1    12   
1    outdegree centrality    0.0   Head-Tail  Female  CCvsCC  CC1_2    12   
2    outdegree centrality    0.0   Head-Tail  Female  CCvsCC  CC1_3    12   
3    outdegree centrality    0.4   Head-Tail  Female  CCvsCC  CC2_1    12   
4    outdegree centrality    0.8   Head-Tail  Female  CCvsCC  CC2_2    12   
..                    ...    ...         ...     ...     ...    ...   ...   
205  outdegree centrality    0.4   Head-Tail  Female  CCvsCC  CC1_2    12   
206  outdegree centrality    0.0   Head-Tail  Female  CCvsCC  CC1_3    12   
207  outdegree centrality    0.4   Head-Tail  Female  CCvsCC  CC2_1    12   
208  outdegree centrality    0.2   Head-Tail  Female  CCvsCC  CC2_2    12   
2

          Network Measure  Score Interaction  Gender  Strain   Care Group  \
0    outdegree centrality    0.2   Head-Tail  Female  CCvsCC  CC1_1    14   
1    outdegree centrality    0.2   Head-Tail  Female  CCvsCC  CC1_2    14   
2    outdegree centrality    0.4   Head-Tail  Female  CCvsCC  CC1_3    14   
3    outdegree centrality    0.2   Head-Tail  Female  CCvsCC  CC2_1    14   
4    outdegree centrality    0.2   Head-Tail  Female  CCvsCC  CC2_2    14   
..                    ...    ...         ...     ...     ...    ...   ...   
199  outdegree centrality    0.8   Head-Tail  Female  CCvsCC  CC1_2    14   
200  outdegree centrality    0.2   Head-Tail  Female  CCvsCC  CC1_3    14   
201  outdegree centrality    0.0   Head-Tail  Female  CCvsCC  CC2_1    14   
202  outdegree centrality    0.2   Head-Tail  Female  CCvsCC  CC2_2    14   
203  outdegree centrality    0.4   Head-Tail  Female  CCvsCC  CC2_3    14   

                                                  File Iteration  \
0    fi

...

           Network Measure  Score       Interaction Gender  Strain   Care  \
0     outdegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC1_1   
1     outdegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC1_2   
2     outdegree centrality    0.0  Oriented-Towards   Male  CCvsCC  CC1_3   
3     outdegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC2_1   
4     outdegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC2_2   
...                    ...    ...               ...    ...     ...    ...   
2731  outdegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC1_2   
2732  outdegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC1_3   
2733  outdegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC2_1   
2734  outdegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC2_2   
2735  outdegree centrality    0.0  Oriented-Towards   Male  CCvsCC  CC2_3   

     Group                                               File Iteration  \


           Network Measure  Score       Interaction Gender  Strain   Care  \
0     outdegree centrality    0.6  Oriented-Towards   Male  CCvsCC  CC1_1   
1     outdegree centrality    0.8  Oriented-Towards   Male  CCvsCC  CC1_2   
2     outdegree centrality    0.0  Oriented-Towards   Male  CCvsCC  CC1_3   
3     outdegree centrality    0.0  Oriented-Towards   Male  CCvsCC  CC2_1   
4     outdegree centrality    0.0  Oriented-Towards   Male  CCvsCC  CC2_2   
...                    ...    ...               ...    ...     ...    ...   
2719  outdegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC1_2   
2720  outdegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC1_3   
2721  outdegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC2_1   
2722  outdegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC2_2   
2723  outdegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC2_3   

     Group                                               File Iteration  \


           Network Measure  Score       Interaction Gender  Strain   Care  \
0     outdegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC1_1   
1     outdegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC1_2   
2     outdegree centrality    0.0  Oriented-Towards   Male  CCvsCC  CC1_3   
3     outdegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC2_1   
4     outdegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC2_2   
...                    ...    ...               ...    ...     ...    ...   
2833  outdegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC1_2   
2834  outdegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC1_3   
2835  outdegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC2_1   
2836  outdegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC2_2   
2837  outdegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC2_3   

     Group                                               File Iteration  \


           Network Measure  Score       Interaction Gender  Strain  Care  \
0     outdegree centrality    0.4  Oriented-Towards   Male  FCvsCC  CC_1   
1     outdegree centrality    0.2  Oriented-Towards   Male  FCvsCC  CC_2   
2     outdegree centrality    0.0  Oriented-Towards   Male  FCvsCC  CC_3   
3     outdegree centrality    0.2  Oriented-Towards   Male  FCvsCC  FC_1   
4     outdegree centrality    0.6  Oriented-Towards   Male  FCvsCC  FC_2   
...                    ...    ...               ...    ...     ...   ...   
1957  outdegree centrality    0.0  Oriented-Towards   Male  FCvsCC  CC_2   
1958  outdegree centrality    0.4  Oriented-Towards   Male  FCvsCC  CC_3   
1959  outdegree centrality    0.0  Oriented-Towards   Male  FCvsCC  FC_1   
1960  outdegree centrality    0.4  Oriented-Towards   Male  FCvsCC  FC_2   
1961  outdegree centrality    0.2  Oriented-Towards   Male  FCvsCC  FC_3   

     Group                                               File Iteration  \
0       45  

           Network Measure  Score       Interaction Gender  Strain  Care  \
0     outdegree centrality    0.6  Oriented-Towards   Male  FCvsCC  CC_1   
1     outdegree centrality    0.2  Oriented-Towards   Male  FCvsCC  CC_2   
2     outdegree centrality    0.6  Oriented-Towards   Male  FCvsCC  CC_3   
3     outdegree centrality    0.0  Oriented-Towards   Male  FCvsCC  FC_1   
4     outdegree centrality    0.0  Oriented-Towards   Male  FCvsCC  FC_2   
...                    ...    ...               ...    ...     ...   ...   
2725  outdegree centrality    0.2  Oriented-Towards   Male  FCvsCC  CC_2   
2726  outdegree centrality    0.0  Oriented-Towards   Male  FCvsCC  CC_3   
2727  outdegree centrality    0.4  Oriented-Towards   Male  FCvsCC  FC_1   
2728  outdegree centrality    0.2  Oriented-Towards   Male  FCvsCC  FC_2   
2729  outdegree centrality    0.2  Oriented-Towards   Male  FCvsCC  FC_3   

     Group                                               File Iteration  \
0       49  

In [10]:
%%time
# def all_treatment_analysis(treatments, All, network_measures, reverse, exponent, tol, rescale, raw, iterations):
# treatments = [["./data/dbs_Head-Tail_20191013.mat"], ["./data/dbs_Head-Head_20191013.mat"], ["./data/dbs_Centers-Close_20191013.mat"], ["./data/dbs_Oriented-Towards_20191013.mat"]]
treatments = [["../data/mat_files/dbs_Head-Tail_20191013.mat"], ["../data/mat_files/dbs_Head-Head_20191013.mat"], ["../data/mat_files/dbs_Centers-Close_20191013.mat"], ["../data/mat_files/dbs_Oriented-Towards_20191013.mat"]]

# treatments = [['../data/mat_files/dbs_Head-Tail_20191013.mat']]
for x in treatments:
    print(x)
    df_zscore_ev_split = all_treatment_analysis(x, False, [['indegree centrality', nx.in_degree_centrality]], False, 0, 1e-07,True, True, 0)

['../data/mat_files/dbs_Head-Tail_20191013.mat']
Properties of current analysis:
Raw:  True
Split groups calculation:  True
Network Measure:  indegree centrality
----------------------
fixed_Male-NacvsCC_3vs3Males_P60_CCvsNAC_Group8V_Interaction_30min_cam_2_Sat_09_07_2019_mjpeg_tracks.mat
../data/mat_files/dbs_Head-Tail_20191013.mat
         Network Measure  Score Interaction Gender   Strain   Care Group  \
0    indegree centrality    0.0   Head-Tail   Male  NACvsCC   CC_1     1   
1    indegree centrality    0.4   Head-Tail   Male  NACvsCC   CC_2     1   
2    indegree centrality    0.4   Head-Tail   Male  NACvsCC   CC_3     1   
3    indegree centrality    0.2   Head-Tail   Male  NACvsCC  Nac_1     1   
4    indegree centrality    0.2   Head-Tail   Male  NACvsCC  Nac_2     1   
..                   ...    ...         ...    ...      ...    ...   ...   
103  indegree centrality    0.4   Head-Tail   Male  NACvsCC   CC_2     1   
104  indegree centrality    0.6   Head-Tail   Male  NACvs

         Network Measure  Score Interaction Gender   Strain   Care Group  \
0    indegree centrality    0.2   Head-Tail   Male  NACvsCC   CC_1     6   
1    indegree centrality    0.0   Head-Tail   Male  NACvsCC   CC_2     6   
2    indegree centrality    0.2   Head-Tail   Male  NACvsCC   CC_3     6   
3    indegree centrality    0.2   Head-Tail   Male  NACvsCC  Nac_1     6   
4    indegree centrality    0.6   Head-Tail   Male  NACvsCC  Nac_2     6   
..                   ...    ...         ...    ...      ...    ...   ...   
139  indegree centrality    0.0   Head-Tail   Male  NACvsCC   CC_2     6   
140  indegree centrality    0.2   Head-Tail   Male  NACvsCC   CC_3     6   
141  indegree centrality    0.2   Head-Tail   Male  NACvsCC  Nac_1     6   
142  indegree centrality    0.2   Head-Tail   Male  NACvsCC  Nac_2     6   
143  indegree centrality    0.4   Head-Tail   Male  NACvsCC  Nac_3     6   

                                                  File Iteration  \
0    fixed_Male-Nac

        Network Measure  Score Interaction  Gender  Strain   Care Group  \
0   indegree centrality    0.6   Head-Tail  Female  CCvsCC  CC1_1    10   
1   indegree centrality    0.6   Head-Tail  Female  CCvsCC  CC1_2    10   
2   indegree centrality    0.0   Head-Tail  Female  CCvsCC  CC1_3    10   
3   indegree centrality    0.4   Head-Tail  Female  CCvsCC  CC2_1    10   
4   indegree centrality    0.0   Head-Tail  Female  CCvsCC  CC2_2    10   
5   indegree centrality    0.0   Head-Tail  Female  CCvsCC  CC2_3    10   
6   indegree centrality    0.4   Head-Tail  Female  CCvsCC  CC1_1    10   
7   indegree centrality    0.6   Head-Tail  Female  CCvsCC  CC1_2    10   
8   indegree centrality    0.0   Head-Tail  Female  CCvsCC  CC1_3    10   
9   indegree centrality    0.4   Head-Tail  Female  CCvsCC  CC2_1    10   
10  indegree centrality    0.2   Head-Tail  Female  CCvsCC  CC2_2    10   
11  indegree centrality    0.0   Head-Tail  Female  CCvsCC  CC2_3    10   
12  indegree centrality  

        Network Measure  Score Interaction  Gender  Strain   Care Group  \
0   indegree centrality    0.2   Head-Tail  Female  CCvsCC  CC1_1    11   
1   indegree centrality    0.4   Head-Tail  Female  CCvsCC  CC1_2    11   
2   indegree centrality    0.4   Head-Tail  Female  CCvsCC  CC1_3    11   
3   indegree centrality    0.0   Head-Tail  Female  CCvsCC  CC2_1    11   
4   indegree centrality    0.2   Head-Tail  Female  CCvsCC  CC2_2    11   
5   indegree centrality    0.4   Head-Tail  Female  CCvsCC  CC2_3    11   
6   indegree centrality    0.2   Head-Tail  Female  CCvsCC  CC1_1    11   
7   indegree centrality    0.4   Head-Tail  Female  CCvsCC  CC1_2    11   
8   indegree centrality    0.4   Head-Tail  Female  CCvsCC  CC1_3    11   
9   indegree centrality    0.0   Head-Tail  Female  CCvsCC  CC2_1    11   
10  indegree centrality    0.2   Head-Tail  Female  CCvsCC  CC2_2    11   
11  indegree centrality    0.4   Head-Tail  Female  CCvsCC  CC2_3    11   
12  indegree centrality  

        Network Measure  Score Interaction  Gender  Strain   Care Group  \
0   indegree centrality    0.0   Head-Tail  Female  CCvsCC  CC1_1    13   
1   indegree centrality    0.8   Head-Tail  Female  CCvsCC  CC1_2    13   
2   indegree centrality    0.2   Head-Tail  Female  CCvsCC  CC1_3    13   
3   indegree centrality    0.4   Head-Tail  Female  CCvsCC  CC2_1    13   
4   indegree centrality    0.0   Head-Tail  Female  CCvsCC  CC2_2    13   
5   indegree centrality    0.2   Head-Tail  Female  CCvsCC  CC2_3    13   
6   indegree centrality    0.0   Head-Tail  Female  CCvsCC  CC1_1    13   
7   indegree centrality    0.6   Head-Tail  Female  CCvsCC  CC1_2    13   
8   indegree centrality    0.2   Head-Tail  Female  CCvsCC  CC1_3    13   
9   indegree centrality    0.4   Head-Tail  Female  CCvsCC  CC2_1    13   
10  indegree centrality    0.0   Head-Tail  Female  CCvsCC  CC2_2    13   
11  indegree centrality    0.4   Head-Tail  Female  CCvsCC  CC2_3    13   
12  indegree centrality  

...

          Network Measure  Score       Interaction Gender  Strain   Care  \
0     indegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC1_1   
1     indegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC1_2   
2     indegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC1_3   
3     indegree centrality    0.0  Oriented-Towards   Male  CCvsCC  CC2_1   
4     indegree centrality    0.6  Oriented-Towards   Male  CCvsCC  CC2_2   
...                   ...    ...               ...    ...     ...    ...   
2731  indegree centrality    0.6  Oriented-Towards   Male  CCvsCC  CC1_2   
2732  indegree centrality    0.0  Oriented-Towards   Male  CCvsCC  CC1_3   
2733  indegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC2_1   
2734  indegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC2_2   
2735  indegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC2_3   

     Group                                               File Iteration  \
0       33  

          Network Measure  Score       Interaction Gender  Strain   Care  \
0     indegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC1_1   
1     indegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC1_2   
2     indegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC1_3   
3     indegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC2_1   
4     indegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC2_2   
...                   ...    ...               ...    ...     ...    ...   
2719  indegree centrality    0.6  Oriented-Towards   Male  CCvsCC  CC1_2   
2720  indegree centrality    0.0  Oriented-Towards   Male  CCvsCC  CC1_3   
2721  indegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC2_1   
2722  indegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC2_2   
2723  indegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC2_3   

     Group                                               File Iteration  \
0       37  

          Network Measure  Score       Interaction Gender  Strain   Care  \
0     indegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC1_1   
1     indegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC1_2   
2     indegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC1_3   
3     indegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC2_1   
4     indegree centrality    0.0  Oriented-Towards   Male  CCvsCC  CC2_2   
...                   ...    ...               ...    ...     ...    ...   
2833  indegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC1_2   
2834  indegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC1_3   
2835  indegree centrality    0.4  Oriented-Towards   Male  CCvsCC  CC2_1   
2836  indegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC2_2   
2837  indegree centrality    0.2  Oriented-Towards   Male  CCvsCC  CC2_3   

     Group                                               File Iteration  \
0       41  

          Network Measure  Score       Interaction Gender  Strain  Care Group  \
0     indegree centrality    0.0  Oriented-Towards   Male  FCvsCC  CC_1    45   
1     indegree centrality    0.4  Oriented-Towards   Male  FCvsCC  CC_2    45   
2     indegree centrality    0.4  Oriented-Towards   Male  FCvsCC  CC_3    45   
3     indegree centrality    0.0  Oriented-Towards   Male  FCvsCC  FC_1    45   
4     indegree centrality    0.2  Oriented-Towards   Male  FCvsCC  FC_2    45   
...                   ...    ...               ...    ...     ...   ...   ...   
1957  indegree centrality    0.6  Oriented-Towards   Male  FCvsCC  CC_2    45   
1958  indegree centrality    0.2  Oriented-Towards   Male  FCvsCC  CC_3    45   
1959  indegree centrality    0.0  Oriented-Towards   Male  FCvsCC  FC_1    45   
1960  indegree centrality    0.2  Oriented-Towards   Male  FCvsCC  FC_2    45   
1961  indegree centrality    0.2  Oriented-Towards   Male  FCvsCC  FC_3    45   

                           

          Network Measure  Score       Interaction Gender  Strain  Care Group  \
0     indegree centrality    0.2  Oriented-Towards   Male  FCvsCC  CC_1    49   
1     indegree centrality    0.2  Oriented-Towards   Male  FCvsCC  CC_2    49   
2     indegree centrality    0.2  Oriented-Towards   Male  FCvsCC  CC_3    49   
3     indegree centrality    0.2  Oriented-Towards   Male  FCvsCC  FC_1    49   
4     indegree centrality    0.4  Oriented-Towards   Male  FCvsCC  FC_2    49   
...                   ...    ...               ...    ...     ...   ...   ...   
2725  indegree centrality    0.4  Oriented-Towards   Male  FCvsCC  CC_2    49   
2726  indegree centrality    0.8  Oriented-Towards   Male  FCvsCC  CC_3    49   
2727  indegree centrality    0.4  Oriented-Towards   Male  FCvsCC  FC_1    49   
2728  indegree centrality    0.0  Oriented-Towards   Male  FCvsCC  FC_2    49   
2729  indegree centrality    0.0  Oriented-Towards   Male  FCvsCC  FC_3    49   

                           

In [ ]:
%%time
# def all_treatment_analysis(treatments, All, network_measures, reverse, exponent, tol, rescale, raw, iterations):
# treatments = [["./data/dbs_Head-Tail_20191013.mat"], ["./data/dbs_Head-Head_20191013.mat"], ["./data/dbs_Centers-Close_20191013.mat"], ["./data/dbs_Oriented-Towards_20191013.mat"]]
treatments = [["../data/mat_files/dbs_Head-Tail_20191013.mat"], ["../data/mat_files/dbs_Head-Head_20191013.mat"], ["../data/mat_files/dbs_Centers-Close_20191013.mat"], ["../data/mat_files/dbs_Oriented-Towards_20191013.mat"]]

# treatments = [['../data/mat_files/dbs_Head-Tail_20191013.mat']]
for x in treatments:
    print(x)
    df_zscore_ev_split = all_treatment_analysis(x, False, [['eigenvector centrality', nx.eigenvector_centrality]], False, 0, 1e-07,True, True, 0)

In [ ]:
%%time

import time
time.ctime()
# def all_treatment_analysis(treatments, All, network_measures, reverse, exponent, tol, rescale, raw, iterations):
# treatments = [["./data/mat_files/dbs_Head-Tail_20191013.mat"], ["./data/dbs_Head-Head_20191013.mat"], ["./data/dbs_Centers-Close_20191013.mat"], ["./data/dbs_Oriented-Towards_20191013.mat"]]
treatments = [["../data/mat_files/dbs_Head-Tail_20191013.mat"], ["../data/mat_files/dbs_Head-Head_20191013.mat"], ["../data/mat_files/dbs_Centers-Close_20191013.mat"], ["../data/mat_files/dbs_Oriented-Towards_20191013.mat"]]

# treatments = [["../data/mat_files/dbs_Head-Tail_20191013.mat"]]
for t in treatments:
    x = [0, 1, -1, 0.1, -0.1]
    for exponent in x:
        df_zscore_ev_split = all_treatment_analysis(t, False, [['power centrality', "NA"]], False, exponent, 1e-07,True, True, 0)

Properties of current analysis:
Raw:  True
Split groups calculation:  True
Network Measure:  power centrality
----------------------
fixed_Male-NacvsCC_3vs3Males_P60_CCvsNAC_Group8V_Interaction_30min_cam_2_Sat_09_07_2019_mjpeg_tracks.mat
../data/mat_files/dbs_Head-Tail_20191013.mat
      Network Measure  Score Interaction Gender   Strain   Care Group  \
0    power centrality  0.000   Head-Tail   Male  NACvsCC   CC_1     1   
1    power centrality  0.250   Head-Tail   Male  NACvsCC   CC_2     1   
2    power centrality  0.000   Head-Tail   Male  NACvsCC   CC_3     1   
3    power centrality  0.125   Head-Tail   Male  NACvsCC  Nac_1     1   
4    power centrality  0.375   Head-Tail   Male  NACvsCC  Nac_2     1   
..                ...    ...         ...    ...      ...    ...   ...   
103  power centrality  0.125   Head-Tail   Male  NACvsCC   CC_2     1   
104  power centrality  0.250   Head-Tail   Male  NACvsCC   CC_3     1   
105  power centrality  0.000   Head-Tail   Male  NACvsCC  Na

      Network Measure  Score Interaction Gender   Strain   Care Group  \
0    power centrality  0.125   Head-Tail   Male  NACvsCC   CC_1     6   
1    power centrality  0.250   Head-Tail   Male  NACvsCC   CC_2     6   
2    power centrality  0.125   Head-Tail   Male  NACvsCC   CC_3     6   
3    power centrality  0.250   Head-Tail   Male  NACvsCC  Nac_1     6   
4    power centrality  0.250   Head-Tail   Male  NACvsCC  Nac_2     6   
..                ...    ...         ...    ...      ...    ...   ...   
139  power centrality  0.125   Head-Tail   Male  NACvsCC   CC_2     6   
140  power centrality  0.125   Head-Tail   Male  NACvsCC   CC_3     6   
141  power centrality  0.125   Head-Tail   Male  NACvsCC  Nac_1     6   
142  power centrality  0.375   Head-Tail   Male  NACvsCC  Nac_2     6   
143  power centrality  0.125   Head-Tail   Male  NACvsCC  Nac_3     6   

                                                  File Iteration  \
0    fixed_Male-NacvsCC_3vs3Males_P60_NacvsCC_Group... 

     Network Measure  Score Interaction  Gender  Strain   Care Group  \
0   power centrality  0.250   Head-Tail  Female  CCvsCC  CC1_1    10   
1   power centrality  0.125   Head-Tail  Female  CCvsCC  CC1_2    10   
2   power centrality  0.000   Head-Tail  Female  CCvsCC  CC1_3    10   
3   power centrality  0.250   Head-Tail  Female  CCvsCC  CC2_1    10   
4   power centrality  0.000   Head-Tail  Female  CCvsCC  CC2_2    10   
5   power centrality  0.375   Head-Tail  Female  CCvsCC  CC2_3    10   
6   power centrality  0.250   Head-Tail  Female  CCvsCC  CC1_1    10   
7   power centrality  0.000   Head-Tail  Female  CCvsCC  CC1_2    10   
8   power centrality  0.000   Head-Tail  Female  CCvsCC  CC1_3    10   
9   power centrality  0.250   Head-Tail  Female  CCvsCC  CC2_1    10   
10  power centrality  0.000   Head-Tail  Female  CCvsCC  CC2_2    10   
11  power centrality  0.500   Head-Tail  Female  CCvsCC  CC2_3    10   
12  power centrality  0.125   Head-Tail  Female  CCvsCC  CC1_1  

     Network Measure  Score Interaction  Gender  Strain   Care Group  \
0   power centrality  0.000   Head-Tail  Female  CCvsCC  CC1_1    11   
1   power centrality  0.000   Head-Tail  Female  CCvsCC  CC1_2    11   
2   power centrality  0.125   Head-Tail  Female  CCvsCC  CC1_3    11   
3   power centrality  0.250   Head-Tail  Female  CCvsCC  CC2_1    11   
4   power centrality  0.375   Head-Tail  Female  CCvsCC  CC2_2    11   
5   power centrality  0.250   Head-Tail  Female  CCvsCC  CC2_3    11   
6   power centrality  0.125   Head-Tail  Female  CCvsCC  CC1_1    11   
7   power centrality  0.000   Head-Tail  Female  CCvsCC  CC1_2    11   
8   power centrality  0.125   Head-Tail  Female  CCvsCC  CC1_3    11   
9   power centrality  0.250   Head-Tail  Female  CCvsCC  CC2_1    11   
10  power centrality  0.250   Head-Tail  Female  CCvsCC  CC2_2    11   
11  power centrality  0.250   Head-Tail  Female  CCvsCC  CC2_3    11   
12  power centrality  0.125   Head-Tail  Female  CCvsCC  CC1_1  

     Network Measure  Score Interaction  Gender  Strain   Care Group  \
0   power centrality  0.125   Head-Tail  Female  CCvsCC  CC1_1    13   
1   power centrality  0.000   Head-Tail  Female  CCvsCC  CC1_2    13   
2   power centrality  0.375   Head-Tail  Female  CCvsCC  CC1_3    13   
3   power centrality  0.250   Head-Tail  Female  CCvsCC  CC2_1    13   
4   power centrality  0.125   Head-Tail  Female  CCvsCC  CC2_2    13   
5   power centrality  0.125   Head-Tail  Female  CCvsCC  CC2_3    13   
6   power centrality  0.125   Head-Tail  Female  CCvsCC  CC1_1    13   
7   power centrality  0.000   Head-Tail  Female  CCvsCC  CC1_2    13   
8   power centrality  0.375   Head-Tail  Female  CCvsCC  CC1_3    13   
9   power centrality  0.250   Head-Tail  Female  CCvsCC  CC2_1    13   
10  power centrality  0.125   Head-Tail  Female  CCvsCC  CC2_2    13   
11  power centrality  0.125   Head-Tail  Female  CCvsCC  CC2_3    13   
12  power centrality  0.125   Head-Tail  Female  CCvsCC  CC1_1  

...

       Network Measure     Score    Interaction Gender  Strain  Care Group  \
0     power centrality -0.000000  Centers-Close   Male  FCvsCC  CC_1    49   
1     power centrality  0.300000  Centers-Close   Male  FCvsCC  CC_2    49   
2     power centrality  0.200000  Centers-Close   Male  FCvsCC  CC_3    49   
3     power centrality  0.300000  Centers-Close   Male  FCvsCC  FC_1    49   
4     power centrality  0.200000  Centers-Close   Male  FCvsCC  FC_2    49   
...                ...       ...            ...    ...     ...   ...   ...   
5101  power centrality  0.285714  Centers-Close   Male  FCvsCC  CC_2    49   
5102  power centrality  0.285714  Centers-Close   Male  FCvsCC  CC_3    49   
5103  power centrality  0.142857  Centers-Close   Male  FCvsCC  FC_1    49   
5104  power centrality -0.000000  Centers-Close   Male  FCvsCC  FC_2    49   
5105  power centrality -0.000000  Centers-Close   Male  FCvsCC  FC_3    49   

                                                   File Iterati

       Network Measure  Score    Interaction Gender   Strain   Care Group  \
0     power centrality   0.00  Centers-Close   Male  NACvsCC   CC_1     1   
1     power centrality   0.25  Centers-Close   Male  NACvsCC   CC_2     1   
2     power centrality   0.25  Centers-Close   Male  NACvsCC   CC_3     1   
3     power centrality   0.25  Centers-Close   Male  NACvsCC  Nac_1     1   
4     power centrality   0.00  Centers-Close   Male  NACvsCC  Nac_2     1   
...                ...    ...            ...    ...      ...    ...   ...   
1927  power centrality  -0.50  Centers-Close   Male  NACvsCC   CC_2     1   
1928  power centrality   0.00  Centers-Close   Male  NACvsCC   CC_3     1   
1929  power centrality   0.00  Centers-Close   Male  NACvsCC  Nac_1     1   
1930  power centrality   0.50  Centers-Close   Male  NACvsCC  Nac_2     1   
1931  power centrality   1.00  Centers-Close   Male  NACvsCC  Nac_3     1   

                                                   File Iteration  \
0     

       Network Measure     Score    Interaction Gender   Strain   Care Group  \
0     power centrality  0.250000  Centers-Close   Male  NACvsCC   CC_1     5   
1     power centrality  0.250000  Centers-Close   Male  NACvsCC   CC_2     5   
2     power centrality  0.250000  Centers-Close   Male  NACvsCC   CC_3     5   
3     power centrality  0.250000  Centers-Close   Male  NACvsCC  Nac_1     5   
4     power centrality  0.000000  Centers-Close   Male  NACvsCC  Nac_2     5   
...                ...       ...            ...    ...      ...    ...   ...   
2227  power centrality  0.142857  Centers-Close   Male  NACvsCC   CC_2     5   
2228  power centrality  0.285714  Centers-Close   Male  NACvsCC   CC_3     5   
2229  power centrality  0.285714  Centers-Close   Male  NACvsCC  Nac_1     5   
2230  power centrality  0.000000  Centers-Close   Male  NACvsCC  Nac_2     5   
2231  power centrality  0.142857  Centers-Close   Male  NACvsCC  Nac_3     5   

                                       

       Network Measure  Score    Interaction Gender   Strain   Care Group  \
0     power centrality   0.25  Centers-Close   Male  NACvsCC   CC_1     9   
1     power centrality   0.25  Centers-Close   Male  NACvsCC   CC_2     9   
2     power centrality   0.25  Centers-Close   Male  NACvsCC   CC_3     9   
3     power centrality   0.00  Centers-Close   Male  NACvsCC  Nac_1     9   
4     power centrality   0.00  Centers-Close   Male  NACvsCC  Nac_2     9   
...                ...    ...            ...    ...      ...    ...   ...   
1855  power centrality   0.25  Centers-Close   Male  NACvsCC   CC_2     9   
1856  power centrality   0.00  Centers-Close   Male  NACvsCC   CC_3     9   
1857  power centrality   0.00  Centers-Close   Male  NACvsCC  Nac_1     9   
1858  power centrality   0.25  Centers-Close   Male  NACvsCC  Nac_2     9   
1859  power centrality   0.25  Centers-Close   Male  NACvsCC  Nac_3     9   

                                                   File Iteration  \
0     

       Network Measure  Score    Interaction  Gender  Strain   Care Group  \
0     power centrality   0.00  Centers-Close  Female  CCvsCC  CC1_1    13   
1     power centrality   0.00  Centers-Close  Female  CCvsCC  CC1_2    13   
2     power centrality   0.00  Centers-Close  Female  CCvsCC  CC1_3    13   
3     power centrality   0.50  Centers-Close  Female  CCvsCC  CC2_1    13   
4     power centrality   1.00  Centers-Close  Female  CCvsCC  CC2_2    13   
...                ...    ...            ...     ...     ...    ...   ...   
1381  power centrality   0.25  Centers-Close  Female  CCvsCC  CC1_2    13   
1382  power centrality   0.25  Centers-Close  Female  CCvsCC  CC1_3    13   
1383  power centrality   0.25  Centers-Close  Female  CCvsCC  CC2_1    13   
1384  power centrality   0.25  Centers-Close  Female  CCvsCC  CC2_2    13   
1385  power centrality   0.00  Centers-Close  Female  CCvsCC  CC2_3    13   

                                                   File Iteration  \
0     

# power centrality z-score

In [42]:
din = [0,1,2,3,4,5]
dout = [5,2,4,3,1,0]
results=np.zeros((6,1000))
for i in range(100):
    done=False
    while not done:
        try:
            #results[:,i] gets column i
            results[:,i]=np.array(list(bonacich_power_centrality(nx.directed_configuration_model(din,dout, create_using=nx.DiGraph()), 1, 1e-07, False).values()))
            done=True
        except:
            False

print(np.mean((results[:,1]-np.mean(results[:,1:],1))/np.std(results[:,1:])))

[ 0.1699974  -4.37496059  2.61839886 -5.71057608  0.92970654  0.        ]


In [ ]:
%%time
# def all_treatment_analysis(treatments, All, network_measures, reverse, exponent, tol, rescale, raw, iterations):
# treatments = [["./data/dbs_Head-Tail_20191013.mat"], ["./data/dbs_Head-Head_20191013.mat"], ["./data/dbs_Centers-Close_20191013.mat"], ["./data/dbs_Oriented-Towards_20191013.mat"]]
treatments = [["./data/dbs_Head-Tail_20191013.mat"]]
for x in treatments:
    print(x)
    df_zscore_ev_split = all_treatment_analysis(x, True, [['bonacich power centrality', "NA"]], False, 0, 1e-07,True, False, 2500)

In [ ]:
%%time
# def all_treatment_analysis(treatments, All, network_measures, reverse, exponent, tol, rescale, raw, iterations):
# treatments = [["./data/dbs_Head-Tail_20191013.mat"], ["./data/dbs_Head-Head_20191013.mat"], ["./data/dbs_Centers-Close_20191013.mat"], ["./data/dbs_Oriented-Towards_20191013.mat"]]
treatments = [["./data/dbs_Head-Tail_20191013.mat"]]
for x in treatments:
    print(x)
    df_zscore_ev_split = all_treatment_analysis(x, True, [['bonacich power centrality', "NA"]], False, -1, 1e-07,True, False, 2500)

In [ ]:
%%time
# def all_treatment_analysis(treatments, All, network_measures, reverse, exponent, tol, rescale, raw, iterations):
# treatments = [["./data/dbs_Head-Tail_20191013.mat"], ["./data/dbs_Head-Head_20191013.mat"], ["./data/dbs_Centers-Close_20191013.mat"], ["./data/dbs_Oriented-Towards_20191013.mat"]]
treatments = [["./data/dbs_Head-Tail_20191013.mat"]]
for x in treatments:
    print(x)
    df_zscore_ev_split = all_treatment_analysis(x, True, [['bonacich power centrality', "NA"]], False, 1, 1e-07,True, False, 2500)

In [ ]:
%%time
# def all_treatment_analysis(treatments, All, network_measures, reverse, exponent, tol, rescale, raw, iterations):
# treatments = [["./data/dbs_Head-Tail_20191013.mat"], ["./data/dbs_Head-Head_20191013.mat"], ["./data/dbs_Centers-Close_20191013.mat"], ["./data/dbs_Oriented-Towards_20191013.mat"]]
treatments = [["./data/dbs_Head-Tail_20191013.mat"]]
for x in treatments:
    print(x)
    df_zscore_ev_split = all_treatment_analysis(x, True, [['bonacich power centrality', "NA"]], False, 0.1, 1e-07,True, False, 2500)